In [2]:
# ## install finrl library
# !pip install wrds
# !pip install swig
# !pip install yfinance==0.2.44
# !pip install -q condacolab
# import condacolab
# condacolab.install()
# !apt-get update -y -qq && apt-get install -y -qq cmake libopenmpi-dev python3-dev zlib1g-dev libgl1-mesa-glx swig
# !pip install git+https://github.com/flpymonkey/FinRL-Fork.git

In [2]:
import warnings
warnings.filterwarnings("ignore")

In [3]:
import pandas as pd
import numpy as np
import matplotlib
import matplotlib.pyplot as plt
# matplotlib.use('Agg')
import datetime

%matplotlib inline
from finrl.config_tickers import DOW_30_TICKER
from finrl.meta.preprocessor.yahoodownloader import YahooDownloader
from finrl.meta.preprocessor.preprocessors import FeatureEngineer, data_split
from finrl.meta.env_stock_trading.env_stocktrading import StockTradingEnv
from finrl.agents.stablebaselines3.models import DRLAgent,DRLEnsembleAgent

from finrl.plot import backtest_stats, backtest_plot, get_daily_return, get_baseline

from pprint import pprint

# import sys
# sys.path.append("../FinRL-Library")

import itertools

In [4]:
import os
from finrl.main import check_and_make_directories
from finrl.config import (
    DATA_SAVE_DIR,
    TRAINED_MODEL_DIR,
    TENSORBOARD_LOG_DIR,
    RESULTS_DIR,
    INDICATORS,
    TRAIN_START_DATE,
    TRAIN_END_DATE,
    TEST_START_DATE,
    TEST_END_DATE,
    TRADE_START_DATE,
    TRADE_END_DATE,
)

check_and_make_directories([DATA_SAVE_DIR, TRAINED_MODEL_DIR, TENSORBOARD_LOG_DIR, RESULTS_DIR])

In [5]:
# TODO, remove DOW from training as it is missing some values in 2019
print(DOW_30_TICKER)

['AXP', 'AMGN', 'AAPL', 'BA', 'CAT', 'CSCO', 'CVX', 'GS', 'HD', 'HON', 'IBM', 'INTC', 'JNJ', 'KO', 'JPM', 'MCD', 'MMM', 'MRK', 'MSFT', 'NKE', 'PG', 'TRV', 'UNH', 'CRM', 'VZ', 'V', 'WBA', 'WMT', 'DIS', 'DOW']


In [6]:
TRAIN_START_DATE = '2009-04-01'
TRAIN_END_DATE = '2021-01-01'
TEST_START_DATE = '2021-01-01'
TEST_END_DATE = '2024-01-01'

from finrl.meta.preprocessor.yahoodownloader import YahooDownloader
from finrl.config_tickers import DOW_30_TICKER


# TODO Drop the DOW stock
value_to_remove = "DOW"
# Create a new list without the specified string
DOW_30_TICKER = [x for x in DOW_30_TICKER if x != value_to_remove]
print(DOW_30_TICKER)

TIME_WINDOW = 40
COMMISSION_FEE_PERCENT = 0.001
INITIAL_CASH = 1000000

# TODO currently an issue with yfiance
# df = YahooDownloader(start_date = TRAIN_START_DATE,
#                      end_date = TEST_END_DATE,
#                      ticker_list = DOW_30_TICKER).fetch_data()

df_list = []

for ticker in DOW_30_TICKER:
    # Fetch data for each ticker
    portfolio_raw_df = YahooDownloader(start_date='2011-01-01',
                                       end_date='2022-12-31',
                                       ticker_list=[ticker]).fetch_data()
    # Append the fetched DataFrame to the list
    df_list.append(portfolio_raw_df)

# Concatenate all DataFrames row-wise
portfolio_raw_df = pd.concat(df_list, axis=0, ignore_index=True)
df = portfolio_raw_df
# Display the concatenated DataFrame
print(portfolio_raw_df)

['AXP', 'AMGN', 'AAPL', 'BA', 'CAT', 'CSCO', 'CVX', 'GS', 'HD', 'HON', 'IBM', 'INTC', 'JNJ', 'KO', 'JPM', 'MCD', 'MMM', 'MRK', 'MSFT', 'NKE', 'PG', 'TRV', 'UNH', 'CRM', 'VZ', 'V', 'WBA', 'WMT', 'DIS']


[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%********

Shape of DataFrame:  (107677, 8)


In [7]:
import pandas as pd
import yfinance as yf

data_df = pd.DataFrame()
num_failures = 0
for tic in DOW_30_TICKER:
      temp_df = yf.download(
          tic, start=TRAIN_START_DATE, end=TEST_END_DATE, proxy=None
      )
      temp_df["tic"] = tic
      print(temp_df)
      if len(temp_df) > 0:
          # data_df = data_df.append(temp_df)
          data_df = pd.concat([data_df, temp_df], axis=0)
      else:
          num_failures += 1
if num_failures == len(DOW_30_TICKER):
    raise ValueError("no data is fetched.")
  # reset the index, we want to use numbers as index instead of dates
data_df = data_df.reset_index()

data_df

[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed

                  Open        High         Low       Close   Adj Close  \
Date                                                                     
2009-04-01   13.340000   14.640000   13.080000   14.440000   11.463932   
2009-04-02   15.260000   15.300000   14.590000   14.980000   11.892637   
2009-04-03   14.800000   15.330000   14.520000   15.330000   12.170499   
2009-04-06   15.080000   15.270000   14.650000   15.160000   12.035540   
2009-04-07   15.120000   15.380000   14.850000   15.010000   11.916451   
...                ...         ...         ...         ...         ...   
2023-12-22  185.639999  186.369995  184.630005  185.570007  183.374313   
2023-12-26  185.960007  186.179993  185.130005  185.960007  183.759705   
2023-12-27  186.139999  187.130005  185.619995  187.059998  184.846664   
2023-12-28  187.119995  188.070007  187.000000  187.800003  185.577927   
2023-12-29  187.750000  188.300003  186.529999  187.339996  185.123367   

              Volume  tic  
Date     


[*********************100%***********************]  1 of 1 completed

                  Open        High         Low       Close   Adj Close  \
Date                                                                     
2009-04-01   48.779999   48.930000   47.099998   48.330002   34.259621   
2009-04-02   49.139999   49.259998   46.599998   47.290001   33.522388   
2009-04-03   47.869999   47.970001   46.080002   46.570000   33.012009   
2009-04-06   46.459999   48.060001   46.369999   47.840000   33.912258   
2009-04-07   47.480000   47.939999   46.889999   47.380001   33.586197   
...                ...         ...         ...         ...         ...   
2023-12-22  280.000000  285.679993  280.000000  284.160004  278.031433   
2023-12-26  284.119995  284.720001  281.670013  283.899994  277.777008   
2023-12-27  284.500000  287.290009  283.350006  286.529999  280.350342   
2023-12-28  287.880005  289.040009  287.630005  288.459991  282.238739   
2023-12-29  287.859985  288.489990  286.390015  288.019989  281.808197   

              Volume   tic  
Date    


[*********************100%***********************]  1 of 1 completed


...

[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed

                 Open       High        Low      Close  Adj Close    Volume  \
Date                                                                          
2009-04-01  28.005365  29.459093  27.977228  29.280895  13.174374  27432137   
2009-04-02  29.740459  30.997231  29.534124  30.443876  13.697634  30753746   
2009-04-03  30.528288  30.865927  30.340710  30.753380  13.836888  17738453   
2009-04-06  30.584560  31.015989  30.406361  30.978474  13.938167  19507639   
2009-04-07  30.321951  30.321951  29.477852  29.749840  13.574414  15480723   
...               ...        ...        ...        ...        ...       ...   
2023-12-22  37.419998  37.779999  37.400002  37.490002  35.147896  13157900   
2023-12-26  37.439999  37.639999  37.310001  37.480000  35.138519  11856600   
2023-12-27  37.330002  37.459999  37.200001  37.310001  34.979141  15267600   
2023-12-28  37.180000  37.720001  37.150002  37.490002  35.147896  14931700   
2023-12-29  37.380001  37.759998  37.320000  37.7000


[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed

                 Open       High        Low      Close  Adj Close    Volume  \
Date                                                                          
2009-04-01  17.126667  17.683332  17.073334  17.606667  12.571255  67957200   
2009-04-02  17.780001  18.190001  17.733334  17.879999  12.766418  65542800   
2009-04-03  17.900000  18.100000  17.650000  17.933332  12.804498  49566900   
2009-04-06  17.803333  17.916668  17.633333  17.809999  12.716436  46532400   
2009-04-07  17.653334  17.673332  17.333332  17.463333  12.468914  42833100   
...               ...        ...        ...        ...        ...       ...   
2023-12-22  51.816666  52.383331  51.720001  52.216667  51.712521  19405500   
2023-12-26  52.216667  52.330002  52.036667  52.136665  51.633289  11679900   
2023-12-27  52.103333  52.650002  52.053333  52.626667  52.118561  19896000   
2023-12-28  52.590000  52.776669  52.500000  52.523335  52.016228  16776000   
2023-12-29  52.509998  52.693333  52.386665  52.5499

Date       Open       High        Low      Close  Adj Close  \
0      2009-04-01  13.340000  14.640000  13.080000  14.440000  11.463932   
1      2009-04-02  15.260000  15.300000  14.590000  14.980000  11.892637   
2      2009-04-03  14.800000  15.330000  14.520000  15.330000  12.170499   
3      2009-04-06  15.080000  15.270000  14.650000  15.160000  12.035540   
4      2009-04-07  15.120000  15.380000  14.850000  15.010000  11.916451   
...           ...        ...        ...        ...        ...        ...   
107672 2023-12-22  91.620003  92.239998  90.750000  91.019997  90.602005   
107673 2023-12-26  90.839996  91.269997  90.599998  90.949997  90.532326   
107674 2023-12-27  90.910004  90.940002  90.040001  90.379997  89.964943   
107675 2023-12-28  90.089996  90.980003  89.970001  90.400002  89.984856   
107676 2023-12-29  90.120003  90.599998  89.860001  90.290001  89.875359   

          Volume  tic  
0       27701800  AXP  
1       27296000  AXP  
2       19195400  AXP  
3       16065100  AXP  
4       18546800  AXP  
...          ...  ...  
107672   9411500  DIS  
107673   8086900  DIS  
107674  11123500  DIS  
107675   8479600  DIS  
107676   9201300  DIS  

[107677 rows x 8 columns]

In [9]:
# Add additional technical indicators
INDICATORS = ['macd',
            'rsi_30',
            'cci_30',
            'dx_30']


FEATURES = ["close", "high", "low", "volume"].extend(INDICATORS)

In [10]:
from finrl.meta.preprocessor.preprocessors import FeatureEngineer
fe = FeatureEngineer(use_technical_indicator=True,
                     tech_indicator_list = INDICATORS,
                     use_turbulence=True,
                     user_defined_feature = False)

processed = fe.preprocess_data(df)
processed = processed.copy()
processed = processed.fillna(0)
processed = processed.replace(np.inf,0)

# here you can see the engineered features are added to each stock day
print(processed)


Successfully added technical indicators
Successfully added turbulence index
              date        open        high         low       close     volume  \
0       2009-04-01    3.717500    3.892857    3.710357    3.278073  589372000   
1       2009-04-01   48.779999   48.930000   47.099998   34.259613   10850100   
2       2009-04-01   13.340000   14.640000   13.080000   11.463933   27701800   
3       2009-04-01   34.520000   35.599998   34.209999   26.850744    9288800   
4       2009-04-01   27.500000   29.520000   27.440001   19.116175   15308300   
...            ...         ...         ...         ...         ...        ...   
107672  2023-12-29  525.979980  528.239990  523.919983  520.342285    2080100   
107673  2023-12-29  260.570007  261.459991  259.670013  258.866302    4074600   
107674  2023-12-29   37.380001   37.759998   37.320000   35.344772   16205200   
107675  2023-12-29   26.440001   26.629999   25.750000   24.868887   10853300   
107676  2023-12-29   52.509998   

In [123]:
stock_dimension = len(processed.tic.unique())
state_space = 1 + 2*stock_dimension + len(INDICATORS)*stock_dimension
print(f"Stock Dimension: {stock_dimension}, State Space: {state_space}")

Stock Dimension: 29, State Space: 175


In [124]:

# Split this on the train and trade test data

train = data_split(processed, TRAIN_START_DATE,TRAIN_END_DATE)
test = data_split(processed, TEST_START_DATE,TEST_END_DATE)
print(len(train))
print(len(test))


train.to_csv('train_data.csv')
test.to_csv('test_data.csv')

85840
21837


In [125]:
import pandas as pd
from stable_baselines3.common.logger import configure

from finrl.agents.stablebaselines3.models import DRLAgent
from finrl.config import TRAINED_MODEL_DIR, RESULTS_DIR
from finrl.main import check_and_make_directories
from finrl.meta.env_stock_trading.env_stocktrading import StockTradingEnv

check_and_make_directories([TRAINED_MODEL_DIR])

In [126]:
# Train the data

train = pd.read_csv('train_data.csv')

# If you are not using the data generated from part 1 of this tutorial, make sure 
# it has the columns and index in the form that could be make into the environment. 
# Then you can comment and skip the following two lines.
train = train.set_index(train.columns[0])
train.index.names = ['']

In [127]:
stock_dimension = len(train.tic.unique())
state_space = 1 + 2*stock_dimension + len(INDICATORS)*stock_dimension
print(f"Stock Dimension: {stock_dimension}, State Space: {state_space}")

Stock Dimension: 29, State Space: 175


In [128]:
buy_cost_list = sell_cost_list = [COMMISSION_FEE_PERCENT] * stock_dimension
num_stock_shares = [0] * stock_dimension

env_kwargs = {
    "hmax": 100,
    "initial_amount": INITIAL_CASH,
    "num_stock_shares": num_stock_shares,
    "buy_cost_pct": buy_cost_list,
    "sell_cost_pct": sell_cost_list,
    "state_space": state_space,
    "stock_dim": stock_dimension,
    "tech_indicator_list": INDICATORS,
    "action_space": stock_dimension,
    "reward_scaling": 1e-4
}


e_train_gym = StockTradingEnv(df = train, **env_kwargs)

In [129]:
env_train, _ = e_train_gym.get_sb_env()
print(type(env_train))

<class 'stable_baselines3.common.vec_env.dummy_vec_env.DummyVecEnv'>


In [130]:
# Train the PPO agent:
# 
#  https://stable-baselines.readthedocs.io/en/master/modules/ppo2.html

agent = DRLAgent(env = env_train)
PPO_PARAMS = {
    "n_steps": 2048,
    #"ent_coef": 0.01,
    "ent_coef": 0.9,
    "learning_rate": 0.00025,
    "batch_size": 128,
    "clip_range": 0.9,

}

# Lower clip_range makes the stocks flatter, very conservative policy

# TODO try playing around with the number of epochs? n_epochs
# TODO try playing around more with the entropy term, make sure agent does enough exploration during training
# TODO try playing around more with the clip papram here


model_ppo = agent.get_model("ppo",model_kwargs = PPO_PARAMS)

# set up logger
tmp_path = RESULTS_DIR + '/ppo'
new_logger_ppo = configure(tmp_path, ["stdout", "csv", "tensorboard"])
# Set new logger
model_ppo.set_logger(new_logger_ppo)

{'n_steps': 2048, 'ent_coef': 0.9, 'learning_rate': 0.00025, 'batch_size': 128, 'clip_range': 0.9}
Using cpu device
Logging to results/ppo


In [131]:
trained_ppo = agent.train_model(model=model_ppo, 
                             tb_log_name='ppo',
                             total_timesteps=10_000)

Original Error: 'obs'
Inner Error: 'reward'
Original Error: 'obs'
Inner Error: 'reward'
Original Error: 'obs'
Inner Error: 'reward'
Original Error: 'obs'
Inner Error: 'reward'
Original Error: 'obs'
Inner Error: 'reward'
Original Error: 'obs'
Inner Error: 'reward'
Original Error: 'obs'
Inner Error: 'reward'
Original Error: 'obs'
Inner Error: 'reward'
Original Error: 'obs'
Inner Error: 'reward'
Original Error: 'obs'
Inner Error: 'reward'
Original Error: 'obs'
Inner Error: 'reward'
Original Error: 'obs'
Inner Error: 'reward'
Original Error: 'obs'
Inner Error: 'reward'
Original Error: 'obs'
Inner Error: 'reward'
Original Error: 'obs'
Inner Error: 'reward'
Original Error: 'obs'
Inner Error: 'reward'
Original Error: 'obs'
Inner Error: 'reward'
Original Error: 'obs'
Inner Error: 'reward'
Original Error: 'obs'
Inner Error: 'reward'
Original Error: 'obs'
Inner Error: 'reward'
Original Error: 'obs'
Inner Error: 'reward'
Original Error: 'obs'
Inner Error: 'reward'
Original Error: 'obs'
Inner Erro

In [132]:
trained_ppo.save(TRAINED_MODEL_DIR + "/agent_ppo")

In [133]:
# Backtest the results


train = pd.read_csv('train_data.csv')
test = pd.read_csv('test_data.csv')

# If you are not using the data generated from part 1 of this tutorial, make sure 
# it has the columns and index in the form that could be make into the environment. 
# Then you can comment and skip the following lines.
train = train.set_index(train.columns[0])
train.index.names = ['']
test = test.set_index(test.columns[0])
test.index.names = ['']

In [134]:
from stable_baselines3 import PPO
from finrl.config import TRAINED_MODEL_DIR

trained_ppo = PPO.load(TRAINED_MODEL_DIR + "/agent_ppo") 

# Here is how to load the model

In [ ]:
# Use this to download from collab

# import shutil
# shutil.make_archive('train', 'zip', '../content')